# RNN 연습예제
# https://github.com/dennybritz/rnn-tutorial-rnnlm

In [1]:
# 젤첨에 readme에 있는거 깔아야 여기는 안넣었지만 theano 라이브러리를 이용한 RNN 적용가능
# 근데 python 2 버전이라 안되는거 오지게 많음 ㅎㅎㅎㅎㅎㅎㅎㅎㅎㅎ


import csv
import itertools
import operator
import numpy as np
import nltk
import sys
from datetime import datetime
from utils import *
# utils 내부에 코딩이 python 2 버전이어서 print 구문에 괄호가 없는 문제를 해결

import matplotlib.pyplot as plt
%matplotlib inline

In [2]:
# NLTK 모델 다운로드 (한번만 하면 됨)
nltk.download("book")

[nltk_data] Downloading collection 'book'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to
[nltk_data]    |     C:\Users\LAY\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\abc.zip.
[nltk_data]    | Downloading package brown to
[nltk_data]    |     C:\Users\LAY\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\brown.zip.
[nltk_data]    | Downloading package chat80 to
[nltk_data]    |     C:\Users\LAY\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\chat80.zip.
[nltk_data]    | Downloading package cmudict to
[nltk_data]    |     C:\Users\LAY\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\cmudict.zip.
[nltk_data]    | Downloading package conll2000 to
[nltk_data]    |     C:\Users\LAY\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\conll2000.zip.
[nltk_data]    | Downloading package conll2002 to
[nltk_data]    |     C:\Users\LAY\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping cor

True

### Language Modeling

Our goal is to build a [Language Model](https://en.wikipedia.org/wiki/Language_model) using a Recurrent Neural Network. Here's what that means. Let's say we have sentence  of $m$ words. Language Model allows us to predict the probability of observing the sentence (in a given dataset) as:

$
\begin{aligned}
P(w_1,...,w_m) = \prod_{i=1}^{m}P(w_i \mid w_1,..., w_{i-1}) 
\end{aligned}
$

In words, the probability of a sentence is the product of probabilities of each word given the words that came before it. So, the probability of the sentence "He went to buy some chocolate" would be the probability of "chocolate" given "He went to buy some", multiplied by the probability of "some" given "He went to buy", and so on. 

Why is that useful? Why would we want to assign a probability to observing a sentence?

First, such a model can be used as a scoring mechanism. For example, a Machine Translation system typically generates multiple candidates for an input sentence. You could use a language model to pick the most probable sentence. Intuitively, the most probable sentence is likely to be grammatically correct. Similar scoring happens in speech recognition systems.

But solving the Language Modeling problem also has a cool side effect. Because we can predict the probability of a word given the preceding words, we are able to generate new text. It's a *generative model*. Given an existing sequence of words we sample a next word from the predicted probabilities, and repeat the process until we have a full sentence. Andrew Karparthy [has a great post](http://karpathy.github.io/2015/05/21/rnn-effectiveness/) that demonstrates what language models are capable of. His models are trained on single characters as opposed to full words, and can generate anything from Shakespeare to Linux Code.

Note that in the above equation the probability of each word is conditioned on **all** previous words. In practice, many models have a hard time representing such long-term dependencies due to computational or memory constraints. They are typically limited to looking at only a few of the previous words. RNNs can, in theory, capture such long-term dependencies, but in practice it's a bit more complex. We'll explore that in a later post.

### Training Data and Preprocessing

To train our language model we need text to learn from. Fortunately we don't need any labels to train a language model, just raw text. I downloaded 15,000 longish reddit comments from a [dataset available on Google's BigQuery](https://bigquery.cloud.google.com/table/fh-bigquery:reddit_comments.2015_08). Text generated by our model will sound like reddit commenters (hopefully)! But as with most Machine Learning projects we first need to do some pre-processing to get our data into the right format.

#### 1. Tokenize Text

We have raw text, but we want to make predictions on a per-word basis. This means we must *tokenize* our comments into sentences, and sentences into words. We could just split each of the comments by spaces, but that wouldn't handle punctuation properly. The sentence "He left!" should be 3 tokens: "He", "left", "!". We'll use [NLTK's](http://www.nltk.org/) `word_tokenize` and `sent_tokenize` methods, which do most of the hard work for us.

#### 2. Remove infrequent words

Most words in our text will only appear one or two times. It's a good idea to remove these infrequent words. Having a huge vocabulary will make our model slow to train (we'll talk about why that is later), and because we don't have a lot of contextual examples for such words we wouldn't be able to learn how to use them correctly anyway. That's quite similar to how humans learn. To really understand how to appropriately use a word you need to have seen it in different contexts.

In our code we limit our vocabulary to the `vocabulary_size` most common words (which I set to 8000, but feel free to change it). We replace all words not included in our vocabulary by `UNKNOWN_TOKEN`. For example, if we don't include the word "nonlinearities" in our vocabulary, the sentence "nonlineraties are important in neural networks" becomes "UNKNOWN_TOKEN are important in Neural Networks". The word `UNKNOWN_TOKEN` will become part of our vocabulary and we will predict it just like any other word. When we generate new text we can replace `UNKNOWN_TOKEN` again, for example by taking a randomly sampled word not in our vocabulary, or we could just generate sentences until we get one that doesn't contain an unknown token.

#### 3. Prepend special start and end tokens

We also want to learn which words tend start and end a sentence. To do this we prepend a special `SENTENCE_START` token, and append a special `SENTENCE_END` token to each sentence. This allows us to ask: Given that the first token is `SENTENCE_START`, what is the likely next word (the actual first word of the sentence)?


#### 4. Build training data matrices

The input to our Recurrent Neural Networks are vectors, not strings. So we create a mapping between words and indices, `index_to_word`, and `word_to_index`. For example,  the word "friendly" may be at index 2001. A training example $x$ may look like `[0, 179, 341, 416]`, where 0 corresponds to `SENTENCE_START`. The corresponding label $y$ would be `[179, 341, 416, 1]`. Remember that our goal is to predict the next word, so y is just the x vector shifted by one position with the last element being the `SENTENCE_END` token. In other words, the correct prediction for word `179` above would be `341`, the actual next word.

In [2]:
# 전체적으로 python 2에서 python 3에 대한 버전 차이로 인한 것들이 많았음. 
# 바꾸는데 별로 어렵진 않았다.

# 데이터 처리

vocabulary_size = 8000
# 전체 단어 갯수 정의, 사용자 임의에 따라 최댓값을 변화시킬 수 있음

unknown_token = "UNKNOWN_TOKEN"
# 정의되지 않은 토큰을 출력하기 위한 것.
# vocabulary에 포함되지 않은 단어는 모두 UNKNOWN_TOKEN으로 출력됨.

sentence_start_token = "SENTENCE_START"
sentence_end_token = "SENTENCE_END"

# Read the data and append SENTENCE_START and SENTENCE_END tokens
print("Reading CSV file...")
with open('data/reddit-comments-2015-08.csv', "r", encoding='UTF8') as f:
    #reddit의 comment를 기반으로 학습해보자~~

    reader = csv.reader(f, skipinitialspace=True)
    next(reader)
    # 긴문자열을 작은문자열(토큰)으로 분리하는 작업
    sentences = itertools.chain(*[nltk.sent_tokenize(x[0].lower()) for x in reader])
    # itertools.chain(): list 를 연결해주는 것
    # lower(): 문자열의 대문자를 소문자로 바꿔주는 작업!
    
    # Append SENTENCE_START and SENTENCE_END
    # sentence의 시작과 끝을 알리기 위한 토큰을 sentence 앞뒤에 붙여주자
    sentences = ["%s %s %s" % (sentence_start_token, x, sentence_end_token) for x in sentences]
    # %s는 string의 공간을 할당해주는 placeholder이다!
    # 총 세개의 string 공간이 할당되어 있는 시스템. 
    
print("Parsed %d sentences." % (len(sentences)))
# %d는 %s와 유사하게 integer에 대한 공간 할당
    
# 시작과 끝을 알리는 토큰 붙이고 다시 토큰화 함
# 왜 또하는거지????
tokenized_sentences = [nltk.word_tokenize(sent) for sent in sentences]

# 단어 빈번도 측정
# 너무 많은 단어를 가지고 있으면 복잡해지므로 빈번도가 낮은 단어들을 없애주기 위한 작업
word_freq = nltk.FreqDist(itertools.chain(*tokenized_sentences))
print("Found %d unique words tokens." % len(word_freq.items()))

# 빈번도가 높은 단어들만 vocabulary 사이즈에 맞춰서 vocab에 넣어줌.
vocab = word_freq.most_common(vocabulary_size-1)

# 선택된 단어들을 indexing 해줌. (index->word, word->index)
index_to_word = [x[0] for x in vocab]
index_to_word.append(unknown_token)
# 이후 우리는 vocabulary에 없는 단어 출력을 위해 내부에 unknown_token도 추가해줌.
word_to_index = dict([(w,i) for i,w in enumerate(index_to_word)])
# enumerate(): 인덱스 값과 리스트 값을 함께 전달해주는 함수


print("Using vocabulary size %d." % vocabulary_size)
print("The least frequent word in our vocabulary is '%s' and appeared %d times." % (vocab[-1][0], vocab[-1][1]))
# 이 프린트 구문은 전체 단어에 대해서가 아니라 우리의 vocabulary 내부에서 가장 빈번도가 적은 단어를 출력하는 구문임

# vocabulary에 없는 단어를 모두 unknown_token으로 바꿔주기 위한 구문.
for i, sent in enumerate(tokenized_sentences):
    tokenized_sentences[i] = [w if w in word_to_index else unknown_token for w in sent]

# 처리 이전의 sentence 출력
print("\nExample sentence: '%s'" % sentences[0])

# 처리 이후 sentence 출력
print("\nExample sentence after Pre-processing: '%s'" % tokenized_sentences[0])

Reading CSV file...
Parsed 79170 sentences.
Found 65408 unique words tokens.
Using vocabulary size 8000.
The least frequent word in our vocabulary is 'documentary' and appeared 10 times.

Example sentence: 'SENTENCE_START i joined a new league this year and they have different scoring rules than i'm used to. SENTENCE_END'

Example sentence after Pre-processing: '['SENTENCE_START', 'i', 'joined', 'a', 'new', 'league', 'this', 'year', 'and', 'they', 'have', 'different', 'scoring', 'rules', 'than', 'i', "'m", 'used', 'to', '.', 'SENTENCE_END']'


In [3]:
# Training을 위한 데이터 만들기
X_train = np.asarray([[word_to_index[w] for w in sent[:-1]] for sent in tokenized_sentences])
y_train = np.asarray([[word_to_index[w] for w in sent[1:]] for sent in tokenized_sentences])

In [4]:
# Training 데이터가 어떻게 생겼는지 출력해보기
x_example, y_example = X_train[17], y_train[17]
print("x:\n%s\n%s" % (" ".join([index_to_word[x] for x in x_example]), x_example))
print("\ny:\n%s\n%s" % (" ".join([index_to_word[x] for x in y_example]), y_example))

x:
SENTENCE_START what are n't you understanding about this ? !
[0, 51, 27, 16, 10, 858, 54, 25, 34, 69]

y:
what are n't you understanding about this ? ! SENTENCE_END
[51, 27, 16, 10, 858, 54, 25, 34, 69, 1]


#### Building the RNN


Let's get concrete and see what the RNN for our language model looks like. The input $x$ will be a sequence of words (just like the example printed above) and each $x_t$ is a single word. But there's one more thing: Because of how matrix multiplication works we can't simply use a word index (like 36) as an input. Instead, we represent each word as a *one-hot vector* of size `vocabulary_size`. For example, the word with index 36 would be the vector of all 0's and a 1 at position 36. So, each $x_t$ will become a vector, and $x$ will be a matrix, with each row representing a word. We'll perform this transformation in our Neural Network code instead of doing it in the pre-processing. The output of our network $o$ has a similar format. Each $o_t$ is a vector of `vocabulary_size` elements, and each element represents the probability of that word being the next word in the sentence.

Let's recap the equations for the RNN from the first part of the tutorial:

$
\begin{aligned}
s_t &= \tanh(Ux_t + Ws_{t-1}) \\
o_t &= \mathrm{softmax}(Vs_t)
\end{aligned}
$

I always find it useful to write down the dimensions of the matrices and vectors. Let's assume we pick a vocabulary size $C = 8000$ and a hidden layer size $H = 100$. You can think of the hidden layer size as the "memory" of our network. Making it bigger allows us to learn more complex patterns, but also results in additional computation. Then we have:

$
\begin{aligned}
x_t & \in \mathbb{R}^{8000} \\
o_t & \in \mathbb{R}^{8000} \\
s_t & \in \mathbb{R}^{100} \\
U & \in \mathbb{R}^{100 \times 8000} \\
V & \in \mathbb{R}^{8000 \times 100} \\
W & \in \mathbb{R}^{100 \times 100} \\
\end{aligned}
$

This is valuable information. Remember that $U,V$ and $W$ are the parameters of our network we want to learn from data. Thus, we need to learn a total of $2HC + H^2$ parameters. In the case of $C=8000$ and $H=100$ that's 1,610,000.  The dimensions also tell us the bottleneck of our model. Note that because $x_t$ is a one-hot vector, multiplying it with $U$ is essentially the same as selecting a column of U, so we don't need to perform the full multiplication. Then, the biggest matrix multiplication in our network is $Vs_t$. That's why we want to keep our vocabulary size small if possible.

Armed with this, it's time to start our implementation.

#### Initialization

We start by declaring a RNN class an initializing our parameters. I'm calling this class `RNNNumpy` because we will implement a Theano version later. Initializing the parameters $U,V$ and $W$ is a bit tricky. We can't just initialize them to 0's because that would result in symmetric calculations in all our layers. We must initialize them randomly. Because proper initialization seems to have an impact on training results there has been lot of research in this area. It turns out that the best initialization depends on the activation function ($\tanh$ in our case) and one [recommended](http://jmlr.org/proceedings/papers/v9/glorot10a/glorot10a.pdf) approach is to initialize the weights randomly in the interval from $\left[-\frac{1}{\sqrt{n}}, \frac{1}{\sqrt{n}}\right]$ where $n$ is the number of incoming connections from the previous layer. This may sound overly complicated, but don't worry too much about it. As long as you initialize your parameters to small random values it typically works out fine.

In [5]:
# RNN 모델링

class RNNNumpy:
    
    def __init__(self, word_dim, hidden_dim=100, bptt_truncate=4):
        # bptt: back propagation through time
        # 현재 시간의 에러를 과거로 역전파하는것
        # 하지만 bptt_truncate를 설정하지 않으면 현재의 에러를 최초까지 역전파시켜 계산량이 높아짐.
        # 그래서 역전파 해주는 타임스텝을 4와 같이 지정해주는 것. 
        # 참고 링크
        # http://solarisailab.com/archives/1451
        
        # Assign instance variables
        self.word_dim = word_dim
        self.hidden_dim = hidden_dim
        self.bptt_truncate = bptt_truncate
        
        # Parameter 초기화
        self.U = np.random.uniform(-np.sqrt(1./word_dim), np.sqrt(1./word_dim), (hidden_dim, word_dim))
        self.V = np.random.uniform(-np.sqrt(1./hidden_dim), np.sqrt(1./hidden_dim), (word_dim, hidden_dim))
        self.W = np.random.uniform(-np.sqrt(1./hidden_dim), np.sqrt(1./hidden_dim), (hidden_dim, hidden_dim))
        

Above, `word_dim` is the size of our vocabulary, and `hidden_dim` is the size of our hidden layer (we can pick it). Don't worry about the `bptt_truncate` parameter for now, we'll explain what that is later.

#### Forward Propagation

Next, let's implement the forward propagation (predicting word probabilities) defined by our equations above:

In [6]:
def forward_propagation(self, x):
    # 전체 타임 스텝
    T = len(x)
    
    # 타임 스텝에 따른 hidden state과 output을 s와 o 함수에 넣어줌. (나중에 사용해주기 위해)
    # We add one additional element for the initial hidden, which we set to 0
    s = np.zeros((T + 1, self.hidden_dim))
    s[-1] = np.zeros(self.hidden_dim)
    
    # The outputs at each time step.
    o = np.zeros((T, self.word_dim))
    # For each time step...
    for t in np.arange(T):
        # Note that we are indexing U by x[t]. This is the same as multiplying U with a one-hot vector.
        s[t] = np.tanh(self.U[:,x[t]] + self.W.dot(s[t-1]))
        
        # 정답값에 대한 확률 분포 계산해줌
        o[t] = softmax(self.V.dot(s[t]))
        
    return [o, s]

RNNNumpy.forward_propagation = forward_propagation

We not only return the calculated outputs, but also the hidden states. We will use them later to calculate the gradients, and by returning them here we avoid duplicate computation. Each $o_t$ is a vector of probabilities representing the words in our vocabulary, but sometimes, for example when evaluating our model, all we want is the next word with the highest probability. We call this function `predict`:

In [7]:
# predict 함수 생성, hot-encoding에서 가장 높은 정답값의 위치 출력

def predict(self, x):
    o, s = self.forward_propagation(x)
    return np.argmax(o, axis=1)

RNNNumpy.predict = predict

Let's try our newly implemented methods and see an example output:

In [8]:
np.random.seed(10)
model = RNNNumpy(vocabulary_size)
o, s = model.forward_propagation(X_train[10])
print(o.shape)
print(o)

(45, 8000)
[[0.00012408 0.0001244  0.00012603 ... 0.00012515 0.00012488 0.00012508]
 [0.00012536 0.00012582 0.00012436 ... 0.00012482 0.00012456 0.00012451]
 [0.00012387 0.0001252  0.00012474 ... 0.00012559 0.00012588 0.00012551]
 ...
 [0.00012471 0.0001243  0.00012524 ... 0.00012475 0.00012522 0.00012623]
 [0.00012564 0.00012431 0.00012481 ... 0.0001244  0.00012609 0.00012486]
 [0.00012447 0.00012509 0.00012469 ... 0.00012473 0.00012506 0.00012641]]


For each word in the sentence (45 above), our model made 8000 predictions representing probabilities of the next word. Note that because we initialized $U,V,W$ to random values these predictions are completely random right now. The following gives the indices of the highest probability predictions for each word:

In [9]:
# 학습 이전에 Train 데이터에 다음 값이 어떤게 올지에 대한 index를 list 형태로 출력
predictions = model.predict(X_train[10])
print(predictions.shape)
print(predictions)

(45,)
[1284 5221 7653 7430 1013 3562 7366 1874  224 6601 7299 6722 6892 3198
 4480 5853 2926  261 4073 2371 6299 5376 4146 3761 7051 5981 1549 3765
 4958 1835 6166 5192 2579 5879 4864 5132 6569 2800 2752 6821 4437 7021
 3943 6912 3922]


#### Calculating the Loss

To train our network we need a way to measure the errors it makes. We call this the loss function $L$, and our goal is find the parameters $U,V$ and $W$ that minimize the loss function for our training data. A common choice for the loss function is the [cross-entropy loss](https://en.wikipedia.org/wiki/Cross_entropy#Cross-entropy_error_function_and_logistic_regression). If we have $N$ training examples (words in our text) and $C$ classes (the size of our vocabulary) then the loss with respect to our predictions $o$ and the true labels $y$ is given by:

$
\begin{aligned}
L(y,o) = - \frac{1}{N} \sum_{n \in N} y_{n} \log o_{n}
\end{aligned}
$

The formula looks a bit complicated, but all it really does is sum over our training examples and add to the loss based on how off our prediction are. The further away $y$ (the correct words) and $o$ (our predictions), the greater the loss will be. We implement the function `calculate_loss`:

In [10]:
def calculate_total_loss(self, x, y):
    L = 0
    # 각 sentence에 대해 진행
    for i in np.arange(len(y)):
        o, s = self.forward_propagation(x[i])
        # We only care about our prediction of the "correct" words
        correct_word_predictions = o[np.arange(len(y[i])), y[i]]
        L += -1 * np.sum(np.log(correct_word_predictions))
        # 위 설명의 loss 계산 함수를 적용
    return L

def calculate_loss(self, x, y):
    # 전체 loss를 training 갯수로 나눠줌
    N = np.sum((len(y_i) for y_i in y))
    return self.calculate_total_loss(x,y)/N

RNNNumpy.calculate_total_loss = calculate_total_loss
RNNNumpy.calculate_loss = calculate_loss

Let's take a step back and think about what the loss should be for random predictions. That will give us a baseline and make sure our implementation is correct. We have $C$ words in our vocabulary, so each word should be (on average) predicted with probability $1/C$, which would yield a loss of $L = -\frac{1}{N} N \log\frac{1}{C} = \log C$:

In [12]:
# Limit to 1000 examples to save time
print("Expected Loss for random predictions: %f" % np.log(vocabulary_size))
# 단순히 예상 loss는 vocabulary 전체 사이즈와 상관관계 

print("Actual loss: %f" % model.calculate_loss(X_train[:1000], y_train[:1000]))
# 학습 이전에 training 데이터에 대한 loss

# 예상 loss와 실제 loss가 비슷한 값을 보임

Expected Loss for random predictions: 8.987197


C:\Users\LAY\Anaconda3\lib\site-packages\ipykernel_launcher.py:14: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  


Actual loss: 8.987393


Pretty close! Keep in mind that evaluating the loss on the full dataset is an expensive operation and can take hours if you have a lot of data!

#### Training the RNN with SGD and Backpropagation Through Time (BPTT)

Remember that we want to find the parameters $U,V$ and $W$ that minimize the total loss on the training data. The most common way to do this is SGD, Stochastic Gradient Descent. The idea behind SGD is pretty simple. We iterate over all our training examples and during each iteration we nudge the parameters into a direction that reduces the error. These directions are given by the gradients on the loss: $\frac{\partial L}{\partial U}, \frac{\partial L}{\partial V}, \frac{\partial L}{\partial W}$. SGD also needs a *learning rate*, which defines how big of a step we want to make in each iteration. SGD is the most popular optimization method not only for Neural Networks, but also for many other Machine Learning algorithms. As such there has been a lot of research on how to optimize SGD using batching, parallelism and adaptive learning rates. Even though the basic idea is simple, implementing SGD in a really efficient way can become very complex. If you want to learn more about SGD [this](http://cs231n.github.io/optimization-1/) is a good place to start. Due to its popularity there are a wealth of tutorials floating around the web, and I don't want to duplicate them here. I'll implement a simple version of SGD that should be understandable even without a background in optimization.

But how do we calculate those gradients we mentioned above? In a [traditional Neural Network](http://www.wildml.com/2015/09/implementing-a-neural-network-from-scratch/) we do this through the backpropagation algorithm. In RNNs we use a slightly modified version of the this algorithm called Backpropagation Through Time (BPTT). Because the parameters are shared by all time steps in the network, the gradient at each output depends not only on the calculations of the current time step, but also the previous time steps. If you know calculus, it really is just applying the chain rule. The next part of the tutorial will be all about BPTT, so I won't go into detailed derivation here. For a general introduction to backpropagation check out [this](http://colah.github.io/posts/2015-08-Backprop/) and this [post](http://cs231n.github.io/optimization-2/). For now you can treat BPTT as a black box. It takes as input a training example $(x,y)$ and returns the gradients $\frac{\partial L}{\partial U}, \frac{\partial L}{\partial V}, \frac{\partial L}{\partial W}$.

In [13]:
def bptt(self, x, y):
    T = len(y)
    # Perform forward propagation
    o, s = self.forward_propagation(x)
    
    # We accumulate the gradients in these variables
    dLdU = np.zeros(self.U.shape)
    dLdV = np.zeros(self.V.shape)
    dLdW = np.zeros(self.W.shape)
    delta_o = o
    delta_o[np.arange(len(y)), y] -= 1.
    
    # For each output backwards...
    for t in np.arange(T)[::-1]:
        #[::-1] 처음부터 끝까지 -1칸 간격으로 (==역순으로)
        dLdV += np.outer(delta_o[t], s[t].T)
        # np.outer: outer product of two vectors
        # 글로 적기 복잡하므로 링크
        # https://het.as.utexas.edu/HET/Software/Numpy/reference/generated/numpy.outer.html
        
        # 초기 델타값 계산
        delta_t = self.V.T.dot(delta_o[t]) * (1 - (s[t] ** 2))
        
        # Backpropagation through time (for at most self.bptt_truncate steps)
        for bptt_step in np.arange(max(0, t-self.bptt_truncate), t+1)[::-1]:
            print("Backpropagation step t=%d bptt step=%d " % (t, bptt_step))
            dLdW += np.outer(delta_t, s[bptt_step-1])              
            dLdU[:,x[bptt_step]] += delta_t
            # 델타 값 업데이트
            delta_t = self.W.T.dot(delta_t) * (1 - s[bptt_step-1] ** 2)
    return [dLdU, dLdV, dLdW]

RNNNumpy.bptt = bptt

#### Gradient Checking

Whenever you implement backpropagation it is good idea to also implement *gradient checking*, which is a way of verifying that your implementation is correct. The idea behind gradient checking is that derivative of a parameter is equal to the slope at the point, which we can approximate by slightly changing the parameter and then dividing by the change:

$
\begin{aligned}
\frac{\partial L}{\partial \theta} \approx \lim_{h \to 0} \frac{J(\theta + h) - J(\theta -h)}{2h}
\end{aligned}
$

We then compare the gradient we calculated using backpropagation to the gradient we estimated with the method above. If there's no large difference we are good. The approximation needs to calculate the total loss for *every* parameter, so that gradient checking is very expensive (remember, we had more than a million parameters in the example above). So it's a good idea to perform it on a model with a smaller vocabulary.

In [14]:
# 경사하강법이 잘되고 있나 체크해보자

def gradient_check(self, x, y, h=0.001, error_threshold=0.01):
    bptt_gradients = model.bptt(x, y)
    
    # 체크 하고 싶은 parameter 리스트로 만들기
    model_parameters = ['U', 'V', 'W']
    
    # Gradient check for each parameter
    for pidx, pname in enumerate(model_parameters):
        # Get the actual parameter value from the mode, e.g. model.W
        parameter = operator.attrgetter(pname)(self)
        print("Performing gradient check for parameter %s with size %d." % (pname, np.prod(parameter.shape)))

        # Iterate over each element of the parameter matrix, e.g. (0,0), (0,1), ...
        it = np.nditer(parameter, flags=['multi_index'], op_flags=['readwrite'])
        while not it.finished:
            ix = it.multi_index
            # Save the original value so we can reset it later
            original_value = parameter[ix]
            # Estimate the gradient using (f(x+h) - f(x-h))/(2*h)
            parameter[ix] = original_value + h
            gradplus = model.calculate_total_loss([x],[y])
            parameter[ix] = original_value - h
            gradminus = model.calculate_total_loss([x],[y])
            estimated_gradient = (gradplus - gradminus)/(2*h)
            # Reset parameter to original value
            parameter[ix] = original_value
            # The gradient for this parameter calculated using backpropagation
            backprop_gradient = bptt_gradients[pidx][ix]
            # calculate The relative error: (|x - y|/(|x| + |y|))
            relative_error = np.abs(backprop_gradient - estimated_gradient)/(np.abs(backprop_gradient) + np.abs(estimated_gradient))
            # If the error is to large fail the gradient check
            if relative_error > error_threshold:
                print("Gradient Check ERROR: parameter=%s ix=%s" % (pname, ix))
                print("+h Loss: %f" % gradplus)
                print("-h Loss: %f" % gradminus)
                print("Estimated_gradient: %f" % estimated_gradient)
                print("Backpropagation gradient: %f" % backprop_gradient)
                print("Relative Error: %f" % relative_error)
                return 
            it.iternext()
        print("Gradient check for parameter %s passed." % (pname))
        # 에러값이 threshold 보다 작다면 이 프린트구문 출력.

RNNNumpy.gradient_check = gradient_check

# To avoid performing millions of expensive calculations we use a smaller vocabulary size for checking.
grad_check_vocab_size = 100
np.random.seed(10)
model = RNNNumpy(grad_check_vocab_size, 10, bptt_truncate=1000)
model.gradient_check([0,1,2,3], [1,2,3,4])

Backpropagation step t=3 bptt step=3 
Backpropagation step t=3 bptt step=2 
Backpropagation step t=3 bptt step=1 
Backpropagation step t=3 bptt step=0 
Backpropagation step t=2 bptt step=2 
Backpropagation step t=2 bptt step=1 
Backpropagation step t=2 bptt step=0 
Backpropagation step t=1 bptt step=1 
Backpropagation step t=1 bptt step=0 
Backpropagation step t=0 bptt step=0 
Performing gradient check for parameter U with size 1000.


C:\Users\LAY\Anaconda3\lib\site-packages\ipykernel_launcher.py:32: RuntimeWarning: invalid value encountered in double_scalars


Gradient check for parameter U passed.
Performing gradient check for parameter V with size 1000.
Gradient check for parameter V passed.
Performing gradient check for parameter W with size 100.
Gradient check for parameter W passed.


#### SGD Implementation

Now that we are able to calculate the gradients for our parameters we can implement SGD. I like to do this in two steps: 1. A function `sdg_step` that calculates the gradients and performs the updates for one batch. 2. An outer loop that iterates through the training set and adjusts the learning rate.

In [15]:
# 경사하강법 일단 한개만 해보기

def numpy_sdg_step(self, x, y, learning_rate):
    # Calculate the gradients
    dLdU, dLdV, dLdW = self.bptt(x, y)
    # Change parameters according to gradients and learning rate
    self.U -= learning_rate * dLdU
    self.V -= learning_rate * dLdV
    self.W -= learning_rate * dLdW

RNNNumpy.sgd_step = numpy_sdg_step

In [16]:
# Outer SGD Loop
# - model: The RNN model instance
# - X_train: The training data set
# - y_train: The training data labels
# - learning_rate: Initial learning rate for SGD
# - nepoch: Number of times to iterate through the complete dataset
# - evaluate_loss_after: Evaluate the loss after this many epochs
def train_with_sgd(model, X_train, y_train, learning_rate=0.005, nepoch=100, evaluate_loss_after=5):
    # loss를 리스트로 저장해서 loss가 어떻게 변하는지 나중에 그래프로 그릴거임
    losses = []
    num_examples_seen = 0
    for epoch in range(nepoch):
        # Optionally evaluate the loss
        if (epoch % evaluate_loss_after == 0):
            loss = model.calculate_loss(X_train, y_train)
            losses.append((num_examples_seen, loss))
            time = datetime.now().strftime('%Y-%m-%d %H:%M:%S')
            print("%s: Loss after num_examples_seen=%d epoch=%d: %f" % (time, num_examples_seen, epoch, loss))
            # Adjust the learning rate if loss increases
            if (len(losses) > 1 and losses[-1][1] > losses[-2][1]):
                learning_rate = learning_rate * 0.5  
                print("Setting learning rate to %f" % learning_rate)
            sys.stdout.flush()
        # For each training example...
        for i in range(len(y_train)):
            # One SGD step
            model.sgd_step(X_train[i], y_train[i], learning_rate)
            num_examples_seen += 1

Done! Let's try to get a sense of how long it would take to train our network:

In [17]:
# 경사하강법 돌리는데 시간 얼마나걸리는지 확인
np.random.seed(10)
model = RNNNumpy(vocabulary_size)
%timeit model.sgd_step(X_train[10], y_train[10], 0.005)

Backpropagation step t=44 bptt step=44 
Backpropagation step t=44 bptt step=43 
Backpropagation step t=44 bptt step=42 
Backpropagation step t=44 bptt step=41 
Backpropagation step t=44 bptt step=40 
Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 
Backpropagation step t=42 bptt step=39 
Backpropagation step t=42 bptt step=38 
Backpropagation step t=41 bptt step=41 
Backpropagation step t=41 bptt step=40 
Backpropagation step t=41 bptt step=39 
Backpropagation step t=41 bptt step=38 
Backpropagation step t=41 bptt step=37 
Backpropagation step t=40 bptt step=40 
Backpropagation step t=40 bptt step=39 
Backpropagation step t=40 bptt step=38 
Backpropagation step t=40 bptt step=37 
Backpropagation step t=40 bptt step=36 


Backpropagation step t=44 bptt step=44 
Backpropagation step t=44 bptt step=43 
Backpropagation step t=44 bptt step=42 
Backpropagation step t=44 bptt step=41 
Backpropagation step t=44 bptt step=40 
Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 
Backpropagation step t=42 bptt step=39 
Backpropagation step t=42 bptt step=38 
Backpropagation step t=41 bptt step=41 
Backpropagation step t=41 bptt step=40 
Backpropagation step t=41 bptt step=39 
Backpropagation step t=41 bptt step=38 
Backpropagation step t=41 bptt step=37 
Backpropagation step t=40 bptt step=40 
Backpropagation step t=40 bptt step=39 
Backpropagation step t=40 bptt step=38 
Backpropagation step t=40 bptt step=37 
Backpropagation step t=40 bptt step=36 


Backpropagation step t=44 bptt step=44 
Backpropagation step t=44 bptt step=43 
Backpropagation step t=44 bptt step=42 
Backpropagation step t=44 bptt step=41 
Backpropagation step t=44 bptt step=40 
Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 
Backpropagation step t=42 bptt step=39 
Backpropagation step t=42 bptt step=38 
Backpropagation step t=41 bptt step=41 
Backpropagation step t=41 bptt step=40 
Backpropagation step t=41 bptt step=39 
Backpropagation step t=41 bptt step=38 
Backpropagation step t=41 bptt step=37 
Backpropagation step t=40 bptt step=40 
Backpropagation step t=40 bptt step=39 
Backpropagation step t=40 bptt step=38 
Backpropagation step t=40 bptt step=37 
Backpropagation step t=40 bptt step=36 


Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 
Backpropagation step t=42 bptt step=39 
Backpropagation step t=42 bptt step=38 
Backpropagation step t=41 bptt step=41 
Backpropagation step t=41 bptt step=40 
Backpropagation step t=41 bptt step=39 
Backpropagation step t=41 bptt step=38 
Backpropagation step t=41 bptt step=37 
Backpropagation step t=40 bptt step=40 
Backpropagation step t=40 bptt step=39 
Backpropagation step t=40 bptt step=38 
Backpropagation step t=40 bptt step=37 
Backpropagation step t=40 bptt step=36 
Backpropagation step t=39 bptt step=39 
Backpropagation step t=39 bptt step=38 
Backpropagation step t=39 bptt step=37 
Backpropagation step t=39 bptt step=36 
Backpropagation step t=39 bptt step=35 


Backpropagation step t=44 bptt step=40 
Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 
Backpropagation step t=42 bptt step=39 
Backpropagation step t=42 bptt step=38 
Backpropagation step t=41 bptt step=41 
Backpropagation step t=41 bptt step=40 
Backpropagation step t=41 bptt step=39 
Backpropagation step t=41 bptt step=38 
Backpropagation step t=41 bptt step=37 
Backpropagation step t=40 bptt step=40 
Backpropagation step t=40 bptt step=39 
Backpropagation step t=40 bptt step=38 
Backpropagation step t=40 bptt step=37 
Backpropagation step t=40 bptt step=36 
Backpropagation step t=39 bptt step=39 
Backpropagation step t=39 bptt step=38 
Backpropagation step t=39 bptt step=37 
Backpropagation step t=39 bptt step=36 


Backpropagation step t=44 bptt step=41 
Backpropagation step t=44 bptt step=40 
Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 
Backpropagation step t=42 bptt step=39 
Backpropagation step t=42 bptt step=38 
Backpropagation step t=41 bptt step=41 
Backpropagation step t=41 bptt step=40 
Backpropagation step t=41 bptt step=39 
Backpropagation step t=41 bptt step=38 
Backpropagation step t=41 bptt step=37 
Backpropagation step t=40 bptt step=40 
Backpropagation step t=40 bptt step=39 
Backpropagation step t=40 bptt step=38 
Backpropagation step t=40 bptt step=37 
Backpropagation step t=40 bptt step=36 
Backpropagation step t=39 bptt step=39 
Backpropagation step t=39 bptt step=38 
Backpropagation step t=39 bptt step=37 


Backpropagation step t=44 bptt step=44 
Backpropagation step t=44 bptt step=43 
Backpropagation step t=44 bptt step=42 
Backpropagation step t=44 bptt step=41 
Backpropagation step t=44 bptt step=40 
Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 
Backpropagation step t=42 bptt step=39 
Backpropagation step t=42 bptt step=38 
Backpropagation step t=41 bptt step=41 
Backpropagation step t=41 bptt step=40 
Backpropagation step t=41 bptt step=39 
Backpropagation step t=41 bptt step=38 
Backpropagation step t=41 bptt step=37 
Backpropagation step t=40 bptt step=40 
Backpropagation step t=40 bptt step=39 
Backpropagation step t=40 bptt step=38 
Backpropagation step t=40 bptt step=37 
Backpropagation step t=40 bptt step=36 


Backpropagation step t=44 bptt step=44 
Backpropagation step t=44 bptt step=43 
Backpropagation step t=44 bptt step=42 
Backpropagation step t=44 bptt step=41 
Backpropagation step t=44 bptt step=40 
Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 
Backpropagation step t=42 bptt step=39 
Backpropagation step t=42 bptt step=38 
Backpropagation step t=41 bptt step=41 
Backpropagation step t=41 bptt step=40 
Backpropagation step t=41 bptt step=39 
Backpropagation step t=41 bptt step=38 
Backpropagation step t=41 bptt step=37 
Backpropagation step t=40 bptt step=40 
Backpropagation step t=40 bptt step=39 
Backpropagation step t=40 bptt step=38 
Backpropagation step t=40 bptt step=37 
Backpropagation step t=40 bptt step=36 


Uh-oh, bad news. One step of SGD takes approximately 350 milliseconds on my laptop. We have about 80,000 examples in our training data, so one epoch (iteration over the whole data set) would take several hours. Multiple epochs would take days, or even weeks! And we're still working with a small dataset compared to what's being used by many of the companies and researchers out there. What now?

Fortunately there are many ways to speed up our code. We could stick with the same model and make our code run faster, or we could modify our model to be less computationally expensive, or both. Researchers have identified many ways to make models less computationally expensive, for example by using a hierarchical softmax or adding projection layers to avoid the large matrix multiplications (see also [here](http://arxiv.org/pdf/1301.3781.pdf) or [here](http://www.fit.vutbr.cz/research/groups/speech/publi/2011/mikolov_icassp2011_5528.pdf)). But I want to keep our model simple and go the first route: Make our implementation run faster using a GPU. Before doing that though, let's just try to run SGD with a small dataset and check if the loss actually decreases:

In [18]:
# 한개 돌리는데 시간 엄청 많이 걸림..
# 그러므로 트레이닝을 조금 적은 데이터로 해보기 (그래도 오래걸림;)

np.random.seed(10)
model = RNNNumpy(vocabulary_size)
losses = train_with_sgd(model, X_train[:100], y_train[:100], nepoch=10, evaluate_loss_after=1)

C:\Users\LAY\Anaconda3\lib\site-packages\ipykernel_launcher.py:14: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  


2020-01-22 01:22:13: Loss after num_examples_seen=0 epoch=0: 8.987280
Backpropagation step t=19 bptt step=19 
Backpropagation step t=19 bptt step=18 
Backpropagation step t=19 bptt step=17 
Backpropagation step t=19 bptt step=16 
Backpropagation step t=19 bptt step=15 
Backpropagation step t=18 bptt step=18 
Backpropagation step t=18 bptt step=17 
Backpropagation step t=18 bptt step=16 
Backpropagation step t=18 bptt step=15 
Backpropagation step t=18 bptt step=14 
Backpropagation step t=17 bptt step=17 
Backpropagation step t=17 bptt step=16 
Backpropagation step t=17 bptt step=15 
Backpropagation step t=17 bptt step=14 
Backpropagation step t=17 bptt step=13 
Backpropagation step t=16 bptt step=16 
Backpropagation step t=16 bptt step=15 
Backpropagation step t=16 bptt step=14 
Backpropagation step t=16 bptt step=13 
Backpropagation step t=16 bptt step=12 
Backpropagation step t=15 bptt step=15 
Backpropagation step t=15 bptt step=14 
Backpropagation step t=15 bptt step=13 
Backpropag

Backpropagation step t=17 bptt step=17 
Backpropagation step t=17 bptt step=16 
Backpropagation step t=17 bptt step=15 
Backpropagation step t=17 bptt step=14 
Backpropagation step t=17 bptt step=13 
Backpropagation step t=16 bptt step=16 
Backpropagation step t=16 bptt step=15 
Backpropagation step t=16 bptt step=14 
Backpropagation step t=16 bptt step=13 
Backpropagation step t=16 bptt step=12 
Backpropagation step t=15 bptt step=15 
Backpropagation step t=15 bptt step=14 
Backpropagation step t=15 bptt step=13 
Backpropagation step t=15 bptt step=12 
Backpropagation step t=15 bptt step=11 
Backpropagation step t=14 bptt step=14 
Backpropagation step t=14 bptt step=13 
Backpropagation step t=14 bptt step=12 
Backpropagation step t=14 bptt step=11 
Backpropagation step t=14 bptt step=10 
Backpropagation step t=13 bptt step=13 
Backpropagation step t=13 bptt step=12 
Backpropagation step t=13 bptt step=11 
Backpropagation step t=13 bptt step=10 
Backpropagation step t=13 bptt step=9 
B

Backpropagation step t=0 bptt step=0 
Backpropagation step t=26 bptt step=26 
Backpropagation step t=26 bptt step=25 
Backpropagation step t=26 bptt step=24 
Backpropagation step t=26 bptt step=23 
Backpropagation step t=26 bptt step=22 
Backpropagation step t=25 bptt step=25 
Backpropagation step t=25 bptt step=24 
Backpropagation step t=25 bptt step=23 
Backpropagation step t=25 bptt step=22 
Backpropagation step t=25 bptt step=21 
Backpropagation step t=24 bptt step=24 
Backpropagation step t=24 bptt step=23 
Backpropagation step t=24 bptt step=22 
Backpropagation step t=24 bptt step=21 
Backpropagation step t=24 bptt step=20 
Backpropagation step t=23 bptt step=23 
Backpropagation step t=23 bptt step=22 
Backpropagation step t=23 bptt step=21 
Backpropagation step t=23 bptt step=20 
Backpropagation step t=23 bptt step=19 
Backpropagation step t=22 bptt step=22 
Backpropagation step t=22 bptt step=21 
Backpropagation step t=22 bptt step=20 
Backpropagation step t=22 bptt step=19 
Ba

Backpropagation step t=2 bptt step=2 
Backpropagation step t=2 bptt step=1 
Backpropagation step t=2 bptt step=0 
Backpropagation step t=1 bptt step=1 
Backpropagation step t=1 bptt step=0 
Backpropagation step t=0 bptt step=0 
Backpropagation step t=15 bptt step=15 
Backpropagation step t=15 bptt step=14 
Backpropagation step t=15 bptt step=13 
Backpropagation step t=15 bptt step=12 
Backpropagation step t=15 bptt step=11 
Backpropagation step t=14 bptt step=14 
Backpropagation step t=14 bptt step=13 
Backpropagation step t=14 bptt step=12 
Backpropagation step t=14 bptt step=11 
Backpropagation step t=14 bptt step=10 
Backpropagation step t=13 bptt step=13 
Backpropagation step t=13 bptt step=12 
Backpropagation step t=13 bptt step=11 
Backpropagation step t=13 bptt step=10 
Backpropagation step t=13 bptt step=9 
Backpropagation step t=12 bptt step=12 
Backpropagation step t=12 bptt step=11 
Backpropagation step t=12 bptt step=10 
Backpropagation step t=12 bptt step=9 
Backpropagatio

...

Backpropagation step t=8 bptt step=8 
Backpropagation step t=8 bptt step=7 
Backpropagation step t=8 bptt step=6 
Backpropagation step t=8 bptt step=5 
Backpropagation step t=8 bptt step=4 
Backpropagation step t=7 bptt step=7 
Backpropagation step t=7 bptt step=6 
Backpropagation step t=7 bptt step=5 
Backpropagation step t=7 bptt step=4 
Backpropagation step t=7 bptt step=3 
Backpropagation step t=6 bptt step=6 
Backpropagation step t=6 bptt step=5 
Backpropagation step t=6 bptt step=4 
Backpropagation step t=6 bptt step=3 
Backpropagation step t=6 bptt step=2 
Backpropagation step t=5 bptt step=5 
Backpropagation step t=5 bptt step=4 
Backpropagation step t=5 bptt step=3 
Backpropagation step t=5 bptt step=2 
Backpropagation step t=5 bptt step=1 
Backpropagation step t=4 bptt step=4 
Backpropagation step t=4 bptt step=3 
Backpropagation step t=4 bptt step=2 
Backpropagation step t=4 bptt step=1 
Backpropagation step t=4 bptt step=0 
Backpropagation step t=3 bptt step=3 
Backpropagat

Backpropagation step t=47 bptt step=44 
Backpropagation step t=47 bptt step=43 
Backpropagation step t=46 bptt step=46 
Backpropagation step t=46 bptt step=45 
Backpropagation step t=46 bptt step=44 
Backpropagation step t=46 bptt step=43 
Backpropagation step t=46 bptt step=42 
Backpropagation step t=45 bptt step=45 
Backpropagation step t=45 bptt step=44 
Backpropagation step t=45 bptt step=43 
Backpropagation step t=45 bptt step=42 
Backpropagation step t=45 bptt step=41 
Backpropagation step t=44 bptt step=44 
Backpropagation step t=44 bptt step=43 
Backpropagation step t=44 bptt step=42 
Backpropagation step t=44 bptt step=41 
Backpropagation step t=44 bptt step=40 
Backpropagation step t=43 bptt step=43 
Backpropagation step t=43 bptt step=42 
Backpropagation step t=43 bptt step=41 
Backpropagation step t=43 bptt step=40 
Backpropagation step t=43 bptt step=39 
Backpropagation step t=42 bptt step=42 
Backpropagation step t=42 bptt step=41 
Backpropagation step t=42 bptt step=40 


Backpropagation step t=0 bptt step=0 
Backpropagation step t=12 bptt step=12 
Backpropagation step t=12 bptt step=11 
Backpropagation step t=12 bptt step=10 
Backpropagation step t=12 bptt step=9 
Backpropagation step t=12 bptt step=8 
Backpropagation step t=11 bptt step=11 
Backpropagation step t=11 bptt step=10 
Backpropagation step t=11 bptt step=9 
Backpropagation step t=11 bptt step=8 
Backpropagation step t=11 bptt step=7 
Backpropagation step t=10 bptt step=10 
Backpropagation step t=10 bptt step=9 
Backpropagation step t=10 bptt step=8 
Backpropagation step t=10 bptt step=7 
Backpropagation step t=10 bptt step=6 
Backpropagation step t=9 bptt step=9 
Backpropagation step t=9 bptt step=8 
Backpropagation step t=9 bptt step=7 
Backpropagation step t=9 bptt step=6 
Backpropagation step t=9 bptt step=5 
Backpropagation step t=8 bptt step=8 
Backpropagation step t=8 bptt step=7 
Backpropagation step t=8 bptt step=6 
Backpropagation step t=8 bptt step=5 
Backpropagation step t=8 bptt

Backpropagation step t=3 bptt step=3 
Backpropagation step t=3 bptt step=2 
Backpropagation step t=3 bptt step=1 
Backpropagation step t=3 bptt step=0 
Backpropagation step t=2 bptt step=2 
Backpropagation step t=2 bptt step=1 
Backpropagation step t=2 bptt step=0 
Backpropagation step t=1 bptt step=1 
Backpropagation step t=1 bptt step=0 
Backpropagation step t=0 bptt step=0 
Backpropagation step t=14 bptt step=14 
Backpropagation step t=14 bptt step=13 
Backpropagation step t=14 bptt step=12 
Backpropagation step t=14 bptt step=11 
Backpropagation step t=14 bptt step=10 
Backpropagation step t=13 bptt step=13 
Backpropagation step t=13 bptt step=12 
Backpropagation step t=13 bptt step=11 
Backpropagation step t=13 bptt step=10 
Backpropagation step t=13 bptt step=9 
Backpropagation step t=12 bptt step=12 
Backpropagation step t=12 bptt step=11 
Backpropagation step t=12 bptt step=10 
Backpropagation step t=12 bptt step=9 
Backpropagation step t=12 bptt step=8 
Backpropagation step t=

Backpropagation step t=22 bptt step=22 
Backpropagation step t=22 bptt step=21 
Backpropagation step t=22 bptt step=20 
Backpropagation step t=22 bptt step=19 
Backpropagation step t=22 bptt step=18 
Backpropagation step t=21 bptt step=21 
Backpropagation step t=21 bptt step=20 
Backpropagation step t=21 bptt step=19 
Backpropagation step t=21 bptt step=18 
Backpropagation step t=21 bptt step=17 
Backpropagation step t=20 bptt step=20 
Backpropagation step t=20 bptt step=19 
Backpropagation step t=20 bptt step=18 
Backpropagation step t=20 bptt step=17 
Backpropagation step t=20 bptt step=16 
Backpropagation step t=19 bptt step=19 
Backpropagation step t=19 bptt step=18 
Backpropagation step t=19 bptt step=17 
Backpropagation step t=19 bptt step=16 
Backpropagation step t=19 bptt step=15 
Backpropagation step t=18 bptt step=18 
Backpropagation step t=18 bptt step=17 
Backpropagation step t=18 bptt step=16 
Backpropagation step t=18 bptt step=15 
Backpropagation step t=18 bptt step=14 


Good, it seems like our implementation is at least doing something useful and decreasing the loss, just like we wanted.

### Generating Text

Now that we have our model we can ask it to generate new text for us! Let's implement a helper function to generate new sentences:

In [20]:
# 테스트를 해보자

def generate_sentence(model):
    # Start token과 함게 시작
    new_sentence = [word_to_index[sentence_start_token]]
    # end token 이 나올때까지 안끝냄
    while not new_sentence[-1] == word_to_index[sentence_end_token]:
        next_word_probs = model.forward_propagation(new_sentence)
        sampled_word = word_to_index[unknown_token]
        # We don't want to sample unknown words
        while sampled_word == word_to_index[unknown_token]:
            samples = np.random.multinomial(1, next_word_probs[-2])
            sampled_word = np.argmax(samples)
        new_sentence.append(sampled_word)
    sentence_str = [index_to_word[x] for x in new_sentence[1:-1]]
    return sentence_str

num_sentences = 10
senten_min_length = 7
# 트레이닝을 작게하고 RNN 구조가 수렴하지 못하는 시스템이어서 결과값이 엉망진창와진창이다 ㅋㅋㅋㅋㅋ
# 여기에서는 다른 라이브러리를 쓰는 방법에 대해서도 소개했는데, 그 라이브러리는 대부분이 python 2에서 지원되는 라이브러리여서 에러가 너무 떠서 못했다.


for i in range(num_sentences):
    sent = []
    # We want long sentences, not sentences with one or two words
    while len(sent) < senten_min_length:
        sent = generate_sentence(model)
    print(" ".join(sent))

SENTENCE_START SENTENCE_START . the , to i a and of you it that is in for n't 's ) ( have but : on with this be are not do if was they as ? or my your just so '' like [ ] ; at he can `` be there you all we about & people from more an get me out one up will 'm when because ! them some no think has 're by - an how n't time http really then gt had does who other only than even also his know % did good * ... been make on much 've which were she should being way see now her out well https game go still him into most going very something too here amp need use 'll say first am over right why where 'd back work on got same better take lot thing things actually use sure never new off though before please ca these pretty i -- ' while someone its down many us since every $ said 2 | post point feel probably always look into two around few # anything might were play best find one ... my may bad getting great different day maybe long could used enough doing give without help both again having having

KeyboardInterrupt: 

A few selected (censored) sentences. I added capitalization.

- Anyway, to the city scene you're an idiot teenager.
- What ? ! ! ! ! ignore!
- Screw fitness, you're saying: https
- Thanks for the advice to keep my thoughts around girls.
- Yep, please disappear with the terrible generation.

Looking at the generated sentences there are a few interesting things to note. The model successfully learn syntax. It properly places commas (usually before and's and or's) and ends sentence with punctuation. Sometimes it mimics internet speech such as multiple exclamation marks or smileys.

However, the vast majority of generated sentences don't make sense or have grammatical errors. One reason could be that we did not train our network long enough (or didn't use enough training data). That may be true, but it's most likely not the main reason. **Our vanilla RNN  can't generate meaningful text because it's unable to learn dependencies between words that are several steps apart**. That's also why RNNs failed to gain popularity when they were first invented. They were beautiful in theory but didn't work well in practice, and we didn't immediately understand why.

Fortunately, the difficulties in training RNNs are [much better understood](http://arxiv.org/abs/1211.5063) now. In the next part of this tutorial we will explore the Backpropagation Through Time (BPTT) algorithm in more detail and demonstrate what's called the *vanishing gradient problem*. This will motivate our move to more sophisticated RNN models, such as LSTMs, which are the current state of the art for many tasks in NLP (and can generate much better reddit comments!).  Everything you learned in this tutorial also applies to LSTMs and other RNN models, so don't feel discouraged if the results for a vanilla RNN are worse then you expected.
